## 2 Ground Control Stations (simple)

This is a first version. The two ground control stations are working in series. 

In [1]:
from helpers import local2global, clean
from simulators import Simulator, Gazebo,ConfigGazebo, QGC
from plan import Plan
from config import Color

clean()

## Create Plans

In [2]:
offsets = [  # east, north, up, heading
    (0., 0., 0., 0.),
    (10., 0., 0., 45.),
    (-5., -10., 0., 225.),
    (-15., 0., 0., 0.),
    (0., -20., 0., 0.),
]
n_blue_veh = 2

n_vehicles = len(offsets)
side_lens = (5, 5, 5, 5, 5)  # must agree with n_vehicles
local_paths = [Plan.create_square_path(side_len=side_len, alt=5) for side_len in side_lens]
plans = [Plan.basic(wps=path, wp_margin=0.5) for path in local_paths]

## Visualization Parameters

In [3]:

homes = [offset[:3] for offset in offsets]
global_paths = [local2global(path, home) for path, home in zip(local_paths, homes)]
models = n_blue_veh*[('iris',Color.BLUE)]+(n_vehicles-n_blue_veh)*[('iris',Color.GREEN)]   # must agree with n_vehicles
markers = [ConfigGazebo.create_trajectory_from_array(array=global_paths[i],color=models[i][1]) for i in range(n_vehicles)]
Gazebo.plot_3d_interactive(markers=markers, title="Simulation Markers", frames=(0.2, 0.2, 0.6), ground=-0.05)

## Choose Simulator

In [4]:
simulator = QGC(offsets=offsets, plans=plans, origin=(-35.3633245, 149.1652241, 0, 0))


simulator = Simulator(offsets=offsets, plans=plans)

gazebo_config = ConfigGazebo(world_path="simulators/gazebo/worlds/runway.world",models=models,markers = markers)
simulator = Gazebo(offsets=offsets,plans=plans,config=gazebo_config)

Launch Simulator

In [5]:
sysids = list(range(1,n_vehicles+1))
gcs_sysids={'blue 🟦':sysids[:n_blue_veh],'green 🟩':sysids[n_blue_veh:]}
orac = simulator.launch(gcs_sysids)

🖥️ Gazebo launched for realistic simulation and 3D visualization.
🚀 ArduPilot SITL vehicle 1 launched (PID 1928830)
🚀 UAV logic for vehicle 1 launched (PID 1928831)
🔗 UAV logic 1 is connected to Ardupilot SITL vehicle 1
🔗 UAV logic 1 is connected to Oracle ⚪
🚀 ArduPilot SITL vehicle 2 launched (PID 1929488)
🚀 UAV logic for vehicle 2 launched (PID 1929489)
🔗 UAV logic 2 is connected to Ardupilot SITL vehicle 2
🔗 UAV logic 2 is connected to Oracle ⚪
🚀 ArduPilot SITL vehicle 3 launched (PID 1929883)
🚀 UAV logic for vehicle 3 launched (PID 1929884)
🔗 UAV logic 3 is connected to Ardupilot SITL vehicle 3
🔗 UAV logic 3 is connected to Oracle ⚪
🚀 ArduPilot SITL vehicle 4 launched (PID 1930141)
🚀 UAV logic for vehicle 4 launched (PID 1930142)
🔗 UAV logic 4 is connected to Ardupilot SITL vehicle 4
🔗 UAV logic 4 is connected to Oracle ⚪
🚀 ArduPilot SITL vehicle 5 launched (PID 1930307)
🚀 UAV logic for vehicle 5 launched (PID 1930308)
🔗 UAV logic 5 is connected to Ardupilot SITL vehicle 5
🔗 UAV lo

## Execute Plans

In [6]:
while len(orac.conns):
    for sysid in list(orac.conns.keys()):
        if orac.is_plan_done(sysid):
            orac.remove(sysid)

✅ Vehicle 1 terminated
✅ Vehicle 3 terminated
✅ Vehicle 4 terminated
✅ Vehicle 2 terminated
✅ Vehicle 5 terminated


## Print Positions gathered

In [7]:
import numpy as np
from numpy.typing import NDArray
from typing import List

import pickle
colors=[Color.BLUE,Color.GREEN] 
for gcs_name,color in zip(gcs_sysids,colors):
    with open(f"trajectories_{gcs_name}.pkl", "rb") as f:
        trajs = pickle.load(f)
    paths:List[NDArray[np.float64]] = []
    for sysid,path in trajs.items():
        paths.append(np.array([x for x in path if x is not None]))
    markers = [ConfigGazebo.create_trajectory_from_array(array=path,color=color) for path in paths]
    Gazebo.plot_3d_interactive(markers=markers,title="Simulation Waypoints",frames=(0.2, 0.2, 0.6),ground=-0.05)